## Creation of Target Database

I am going to create my tables based on my original 3NF database design. 

These tables include users, signal_playbook, signal_recordings_header, and signal_recordings_detail.

In [0]:
#Creating signal_recordings_header table
spark.sql("""CREATE TABLE databases.eshin2.signal_recordings_header (
 signal_ID string NOT NULL,
 play_ID string NOT NULL,
 user_ID string NOT NULL,
 time_stamp timestamp NOT NULL,
 play_name string NOT NULL,
 duration_ms integer NOT NULL)""")

DataFrame[]

In [0]:
#Creating signal_recordings_detail table
#Was originally missing the 9 measurement values for the signal recording sensors in the original database schema design
#Made sure to create a separate signal_recordings_detail table aside from the signal_recordings_header table to include these individual measurements 
spark.sql("""CREATE TABLE databases.eshin2.signal_recordings_detail (
    signal_ID string NOT NULL,
    accel_x double NOT NULL,
    accel_y double NOT NULL,
    accel_z double NOT NULL,
    accel_grav_x double NOT NULL,
    accel_grav_y double NOT NULL,
    accel_grav_z double NOT NULL,
    rotation_rate_alpha double NOT NULL,
    rotation_rate_beta double NOT NULL,
    rotation_rate_gamma double NOT NULL,
    timestamp_ms integer NOT NULL)""")

DataFrame[]

In [0]:
#Creating signal_playbook table
spark.sql("""CREATE TABLE databases.eshin2.signal_playbook (
    play_ID string NOT NULL,
    gesture string NOT NULL,
    historical_context string NOT NULL,
    latin_code_name string NOT NULL,
    mechanic string NOT NULL,
    play_name string NOT NULL,
    translation string NOT NULL,
    play_type string NOT NULL)""")

DataFrame[]

In [0]:
#Creating users table
spark.sql("""CREATE TABLE databases.eshin2.users (
    user_ID string NOT NULL,
    active_course_ID string NOT NULL,
    full_name string NOT NULL,
    age integer NOT NULL,
    email string NOT NULL,
    created_at timestamp NOT NULL,
    active_course_name string NOT NULL,
    updated_at timestamp NOT NULL)""")

DataFrame[]

In [0]:
%sql
---Viewing the signal_recordings_header table
SELECT * FROM databases.eshin2.signal_recordings_header

signal_ID play_ID user_ID time_stamp play_name duration_ms

In [0]:
%sql
---Viewing the signal_recordings_detail table
SELECT * FROM databases.eshin2.signal_recordings_detail

signal_ID accel_x accel_y accel_z accel_grav_x accel_grav_y accel_grav_z rotation_rate_alpha rotation_rate_beta rotation_rate_gamma timestamp_ms

In [0]:
%sql
---Viewing the signal_playbook table
SELECT * FROM databases.eshin2.signal_playbook

play_ID gesture historical_context latin_code_name mechanic play_name translation play_type

In [0]:
%sql
---Viewing the users table
SELECT * FROM databases.eshin2.users

user_ID active_course_ID full_name age email created_at active_course_name updated_at

In [0]:
#The columns that had datatypes of varchar were changed to string instead because Databricks is strict about length constraints with varchar datatypes

## Capture and Store Data Process Implementation

## Import the necessary libaries

[Optionally] Install the firebase-admin SDK for Python.  This is used to connect to the firebase database to get the data for the final project.
- Replace *pip3* with the appropriate python package installer based on your python installation.

In [0]:
#Installing firebase admin for python
!pip3 install firebase-admin

In [0]:
import pandas as pd # Pandas is a python library used for data analysis.
import json #json is a library for dealing with JSON data.
from datetime import datetime # to handle converting the timestamp objects from firebase's SDK to ISO standard.

import firebase_admin
from firebase_admin import credentials, firestore

## Initialize Firebase Admin SDK

The code below assumes the firebase secret credentials, signal_caler.json, is located in the same directly as this notebook.


In [0]:
# Use your service account key JSON file
cred = credentials.Certificate("signal_caller.json")
firebase_admin.initialize_app(cred)

# Get Firestore client
db = firestore.client()

# Utility Functions

In [0]:
# This function recursivlly converts datetime objects from firebase's datetimeWithNanoseconds object type to the ISO8601 standard that works great with Pandas.

def datetimeWithNanoseconds_to_ISO8601(obj):
    """
    Recursively convert DatetimeWithNanoseconds objects to ISO 8601 strings,
    and leave all other values unchanged.

    Args:
        obj: Any Python object (likely a dict, list, or Firestore result) to sanitize.

    Returns:
        A new object with all DatetimeWithNanoseconds values converted to strings.
    """
    from google.cloud.firestore_v1._helpers import DatetimeWithNanoseconds
    from datetime import datetime

    if isinstance(obj, DatetimeWithNanoseconds):
        return obj.isoformat()
    elif isinstance(obj, dict):
        return {k: datetimeWithNanoseconds_to_ISO8601(v) for k, v in obj.items()}
    elif isinstance(obj, list):
        return [datetimeWithNanoseconds_to_ISO8601(i) for i in obj]
    else:
        return obj

# Extract Data from Firebase Database

## Extract Signal Playbook Data

In [0]:
signal_playbook_collection = db.collection('signal_playbook').stream()
signal_playbook_data = {}
for doc in signal_playbook_collection:
    signal_playbook_data[doc.id] = doc.to_dict()

signal_playbook_data = datetimeWithNanoseconds_to_ISO8601(signal_playbook_data)
signal_playbook_data

{'collapse_left': {'gesture': '<',
  'latin_codename': 'Cuneus Deflectere',
  'type': 'Defense',
  'motionGuideImage': '/left.png',
  'mechanic': 'A directional collapse inward from the left — used to break protection schemes and force a disrupted response from the opponent’s offense.',
  'historical_context': 'Mirrors the 1988 goal-line stand vs. Miami. Inches from the goal, the Irish defense locked in with perfect discipline and grit. This call is a tactical reminder of collective pressure and precise execution.',
  'translation': 'Wedge Collapse',
  'name': 'Collapse Left'},
 'irish_surge': {'gesture': 'N',
  'latin_codename': 'Impulsus Ferrum',
  'type': 'Offense',
  'motionGuideImage': '/N.png',
  'mechanic': 'A forward-driving signal that initiates a direct, aggressive push — designed to break through the front line and open a clear path.',
  'historical_context': 'Based on the 2005 “Bush Push” vs. USC. Under extreme pressure, the Irish offense surged with urgency and power. This

## Extract Users Data



In [0]:
users_collection = db.collection('users').stream()
users_data = {}
for doc in users_collection:
    users_data[doc.id] = doc.to_dict()

users_data = datetimeWithNanoseconds_to_ISO8601(users_data)
users_data

{'3T02i8MvMYV0f7Xz7MCnvyLMpLG3': {'age': 27,
  'id': '3T02i8MvMYV0f7Xz7MCnvyLMpLG3',
  'activeCourseId': 'SU25-DS-60620-01',
  'createdAt': '2025-07-09T17:05:35.042000+00:00',
  'email': 'abenedum@nd.edu',
  'activeCourseName': 'Databases and Data Architecture (Summer 2025)',
  'updatedAt': '2025-07-10T14:40:50.519000+00:00',
  'name': 'Andrew Benedum'},
 '7hOsavOpK9hQ53r43R19b8kHxS72': {'age': 32,
  'id': '7hOsavOpK9hQ53r43R19b8kHxS72',
  'activeCourseId': 'SU25-DS-60620-01',
  'createdAt': '2025-06-15T05:06:36.240000+00:00',
  'email': 'btmassoth@gmail.com',
  'activeCourseName': 'Databases and Data Architecture (Summer 2025)',
  'updatedAt': '2025-06-15T05:06:36.240000+00:00',
  'name': 'Bryan Massoth'},
 'A7P5QM0SuEh30sbaJVr4DwwQvpz2': {'age': 43,
  'id': 'A7P5QM0SuEh30sbaJVr4DwwQvpz2',
  'activeCourseId': 'SU25-DS-60620-01',
  'createdAt': '2025-06-15T02:40:21.079000+00:00',
  'email': 'daniel.r.douce@gmail.com',
  'activeCourseName': 'Databases and Data Architecture (Summer 2025)

## Extract the Signal Recordings

This code connects to our Firebase Firestore database and pulls all the documents from the signal_recordings collection.  

Signal Recordings contain the timeseries of sensor measurements.

In [0]:
signal_recording_collection = db.collection('signal_recordings').stream()
signal_recordings_data = {}
for doc in signal_recording_collection:
    signal_recordings_data[doc.id] = doc.to_dict()

signal_recordings_data = datetimeWithNanoseconds_to_ISO8601(signal_recordings_data)

> **signal_recordings_data** is a VERY large dictonary. Don't print the entire thing to your console or you may crash your browser or vscode.

In [0]:
# Safely preview the data in this dictionary
def preview_signals(signal_recordings_data, n=2):
    """
    Pretty-print the first `n` signal recordings, showing all metadata and
    only the first and last measurement rows from the 'data' field.

    Args:
        signal_recordings_data (dict): Dictionary of signal recordings keyed by document ID.
        n (int): Number of signal recordings to preview. Default is 1.

    Notes:
        - Each signal's metadata is fully printed.
        - Only the first and last rows from 'data' are shown for brevity.
    """

    if not signal_recordings_data:
        print("⚠️ No signal recordings found.")
        return

    keys = list(signal_recordings_data.keys())[:n]

    for idx, key in enumerate(keys, 1):
        print(f"\n📄 Signal {idx}: Document ID = {key}\n")

        signal_data = signal_recordings_data[key]

        print("=== Metadata ===")
        for meta_key, meta_value in signal_data.items():
            if meta_key != 'data':
                print(f"{meta_key}: {meta_value}")

        data = signal_data.get("data", [])
        if not data:
            print("⚠️ No signal data found in 'data' field.")
            continue

        print("\n=== First row of data[] ===")
        print(f"[0] {json.dumps(data[0], indent=2)}")

        print("\n=== Last row of data[] ===")
        print(f"[{len(data) - 1}] {json.dumps(data[-1], indent=2)}")


In [0]:
preview_signals(signal_recordings_data)


📄 Signal 1: Document ID = 1DlnbeuO7ggujkFLGkvG

=== Metadata ===
timestamp: 2025-06-15T02:43:36.130000+00:00
playName: Irish Surge
playId: irish_surge
userId: A7P5QM0SuEh30sbaJVr4DwwQvpz2
durationMs: 3935

=== First row of data[] ===
[0] {
  "acceleration": {
    "y": -0.0,
    "z": 0.6000000000000001,
    "x": -0.0
  },
  "accelerationIncludingGravity": {
    "y": 8.6,
    "z": 5.4,
    "x": 0.7000000000000001
  },
  "timestamp": 8,
  "rotationRate": {
    "alpha": -12.7,
    "beta": 1,
    "gamma": 14.100000000000001
  }
}

=== Last row of data[] ===
[233] {
  "acceleration": {
    "y": 1.1,
    "z": -1.2000000000000002,
    "x": 0.7000000000000001
  },
  "accelerationIncludingGravity": {
    "y": 9.8,
    "z": 3.1,
    "x": -0.2
  },
  "timestamp": 3920,
  "rotationRate": {
    "beta": 9.700000000000001,
    "alpha": -8.2,
    "gamma": 3.1
  }
}

📄 Signal 2: Document ID = 1IJGEH5GaHkk1lhJqa8Q

=== Metadata ===
playId: collapse_left
playName: Collapse Left
timestamp: 2025-06-15T02:4

# Transform

TODO: Transform the dictionaries into tables that can then be loaded into your target database.

# Users Data

In [0]:
import pandas as pd

In [0]:
users_data

{'3T02i8MvMYV0f7Xz7MCnvyLMpLG3': {'age': 27,
  'id': '3T02i8MvMYV0f7Xz7MCnvyLMpLG3',
  'activeCourseId': 'SU25-DS-60620-01',
  'createdAt': '2025-07-09T17:05:35.042000+00:00',
  'email': 'abenedum@nd.edu',
  'activeCourseName': 'Databases and Data Architecture (Summer 2025)',
  'updatedAt': '2025-07-10T14:40:50.519000+00:00',
  'name': 'Andrew Benedum'},
 '7hOsavOpK9hQ53r43R19b8kHxS72': {'age': 32,
  'id': '7hOsavOpK9hQ53r43R19b8kHxS72',
  'activeCourseId': 'SU25-DS-60620-01',
  'createdAt': '2025-06-15T05:06:36.240000+00:00',
  'email': 'btmassoth@gmail.com',
  'activeCourseName': 'Databases and Data Architecture (Summer 2025)',
  'updatedAt': '2025-06-15T05:06:36.240000+00:00',
  'name': 'Bryan Massoth'},
 'A7P5QM0SuEh30sbaJVr4DwwQvpz2': {'age': 43,
  'id': 'A7P5QM0SuEh30sbaJVr4DwwQvpz2',
  'activeCourseId': 'SU25-DS-60620-01',
  'createdAt': '2025-06-15T02:40:21.079000+00:00',
  'email': 'daniel.r.douce@gmail.com',
  'activeCourseName': 'Databases and Data Architecture (Summer 2025)

In [0]:
# Flatten Users
rows = []
users_data

# userId
# name
# age
# activeCourseId
# createdAt
# email
# activeCourseName
# updatedAt

rows = []
for user in users_data:
    x = users_data.get(user)
    rows.append(x)

rows

users_df = pd.DataFrame(rows)
users_df

age  ...                           name
0    27  ...                 Andrew Benedum
1    32  ...                  Bryan Massoth
2    43  ...                           d rd
3    30  ...                   Jade Liggett
4    32  ...                Ricardo Ramirez
5    28  ...                Bridget Liesman
6    46  ...                Chris Frederick
7    23  ...                     Sean Lyons
8    31  ...                     Austin Lee
9    26  ...                   Gabby Salera
10   42  ...                Steven Villalon
11   24  ...                 Noah DiRoberto
12   46  ...          Christopher Frederick
13   29  ...                Zach Stabrowski
14   31  ...                    Jack Bremer
15   44  ...                  Jeff Goseland
16   30  ...                 Simone Haywood
17   30  ...                   Jade Liggett
18   28  ...                  Jake Machulcz
19   99  ...                     Paul Drake
20   24  ...                 Mike Mulvihill
21   40  ...  Dinesh Prashanth Varatharajan
22   28  ...                   Darien Geyen
23   35  ...                   Kevin Bursaw
24   46  ...          Christopher Frederick
25   32  ...                  Natasha Malik
26   41  ...              Danielle McDowell
27   43  ...                  Justin Flagel

[28 rows x 8 columns]

In [0]:
#Rearranging columns in the correct order
users_df = users_df[[
    'id',               
    'activeCourseId',   
    'name',             
    'age',
    'email',
    'createdAt',       
    'activeCourseName', 
    'updatedAt'         
]]

In [0]:
#Renaming columns to match the user table created earlier
users_df = users_df.rename(columns={
    'id': 'user_ID',
    'activeCourseId': 'active_course_ID',
    'name': 'full_name',
    'createdAt': 'created_at',
    'activeCourseName': 'active_course_name',
    'updatedAt': 'updated_at'
})

# Signal Playbook Data

In [0]:
#Transforming signal playbook data into a pandas dataframe
import pandas as pd

signal_playbook = {
    'collapse_left': {
        'gesture': '<',
        'latin_codename': 'Cuneus Deflectere',
        'type': 'Defense',
        'motionGuideImage': '/left.png',
        'mechanic': 'A directional collapse inward from the left — used to break protection schemes and force a disrupted response from the opponent’s offense.',
        'historical_context': 'Mirrors the 1988 goal-line stand vs. Miami. Inches from the goal, the Irish defense locked in with perfect discipline and grit. This call is a tactical reminder of collective pressure and precise execution.',
        'translation': 'Wedge Collapse',
        'name': 'Collapse Left'
    },
    'irish_surge': {
        'gesture': 'N',
        'latin_codename': 'Impulsus Ferrum',
        'type': 'Offense',
        'motionGuideImage': '/N.png',
        'mechanic': 'A forward-driving signal that initiates a direct, aggressive push — designed to break through the front line and open a clear path.',
        'historical_context': 'Based on the 2005 “Bush Push” vs. USC. Under extreme pressure, the Irish offense surged with urgency and power. This call reflects Notre Dame’s commitment to driving through adversity to reach the end zone.',
        'translation': 'Iron Surge',
        'name': 'Irish Surge'
    },
    'touchdown_halo': {
        'gesture': 'O (Circle x2)',
        'latin_codename': 'Anima Stadium',
        'type': '12th Man',
        'motionGuideImage': '/O.png',
        'mechanic': 'Double circular motion — boosts team tempo, sync, and field awareness. Used to elevate overall play under crowd-fueled momentum.',
        'historical_context': 'Echoes the 1973 Sugar Bowl when the home crowd’s energy helped launch Tom Clements’ deep pass to victory. This call captures the surge created when the team and its fans are locked in together.',
        'translation': 'Spirit of the Stadium',
        'name': 'Touchdown Halo'
    }
}

#Converting dictionary to DataFrame
signal_playbook_df = pd.DataFrame.from_dict(signal_playbook, orient='index').reset_index()

#Renaming 'index' column to 'play_ID'
signal_playbook_df = signal_playbook_df.rename(columns={'index': 'play_ID'})

#Removing motionGuideImage column
signal_playbook_df = signal_playbook_df.drop(columns=['motionGuideImage'])

signal_playbook_df

play_ID        gesture  ...            translation            name
0   collapse_left              <  ...         Wedge Collapse   Collapse Left
1     irish_surge              N  ...             Iron Surge     Irish Surge
2  touchdown_halo  O (Circle x2)  ...  Spirit of the Stadium  Touchdown Halo

[3 rows x 8 columns]

In [0]:
#Rearranging columns in the correct order
signal_playbook_df = signal_playbook_df[['play_ID',
                                         'gesture', 
                                         'historical_context', 
                                         'latin_codename', 
                                          'mechanic', 
                                          'name', 
                                          'translation', 
                                          'type']]

In [0]:
#Renaming columns to match the signal_playbook table created earlier
signal_playbook_df = signal_playbook_df.rename(columns={'latin_codename': 'latin_code_name',
    'name': 'play_name',
    'type': 'play_type'
})

# Signal Recordings Data

In [0]:
# Flatten Signal Recordings into a Header and Detail Tables
signal_recordings_header = []  # rows for the header
signal_recordings_detail = []  # rows for the detail

for signal in signal_recordings_data:
    signal_dict = signal_recordings_data.get(signal)

    # Header values
    timestamp = signal_dict.get('timestamp')
    playName = signal_dict.get('playName')
    playId = signal_dict.get('playId')
    userId = signal_dict.get('userId')
    durationMs = signal_dict.get('durationMs')

    # Add to header table
    signal_recordings_header.append({
        'signalId': signal,
        'timestamp': timestamp,
        'playName': playName,
        'playId': playId,
        'userId': userId,
        'durationMs': durationMs
    })

    data_list = signal_dict.get('data', [])
    for data_dict in data_list:
        # Extract acceleration
        acceleration = data_dict.get('acceleration', {})
        accel_x = acceleration.get('x')
        accel_y = acceleration.get('y')
        accel_z = acceleration.get('z')

        # Extract acceleration including gravity
        accel_gravity = data_dict.get('accelerationIncludingGravity', {})
        accel_g_x = accel_gravity.get('x')
        accel_g_y = accel_gravity.get('y')
        accel_g_z = accel_gravity.get('z')

        # Extract rotation rate
        rotation = data_dict.get('rotationRate', {})
        rot_alpha = rotation.get('alpha')
        rot_beta = rotation.get('beta')
        rot_gamma = rotation.get('gamma')

        # Extract timestamp (per reading)
        reading_ts = data_dict.get('timestamp')

        # Add to detail table
        signal_recordings_detail.append({
            'signalId': signal,
            'reading_timestamp': reading_ts,
            'accel_x': accel_x,
            'accel_y': accel_y,
            'accel_z': accel_z,
            'accel_g_x': accel_g_x,
            'accel_g_y': accel_g_y,
            'accel_g_z': accel_g_z,
            'rot_alpha': rot_alpha,
            'rot_beta': rot_beta,
            'rot_gamma': rot_gamma
        })

#Converting signal recordings tables to pandas datafram
signal_recordings_header_df = pd.DataFrame(signal_recordings_header)

signal_recordings_detail_df = pd.DataFrame(signal_recordings_detail)

In [0]:
#Renaming columns
signal_recordings_header_df = signal_recordings_header_df.rename(columns={
    'signalId': 'signal_ID',
    'playId': 'play_ID',
    'userId': 'user_ID',
    'timestamp': 'time_stamp',
    'playName': 'play_name',
    'durationMs': 'duration_ms'
})

#Reordering columns
signal_recordings_header_df = signal_recordings_header_df[
    ['signal_ID', 'play_ID', 'user_ID', 'time_stamp', 'play_name', 'duration_ms']
]

#Ensuring that time_stamp is a pandas datetime datatype
signal_recordings_header_df['time_stamp'] = pd.to_datetime(signal_recordings_header_df['time_stamp'])

#Ensuring that duration_ms is a pandas integer type
signal_recordings_header_df['duration_ms'] = signal_recordings_header_df['duration_ms'].astype('Int64') 

In [0]:
#Renaming the columns
signal_recordings_detail_df = signal_recordings_detail_df.rename(columns={
    'signalId': 'signal_ID',
    'accel_g_x': 'accel_grav_x',
    'accel_g_y': 'accel_grav_y',
    'accel_g_z': 'accel_grav_z',
    'rot_alpha': 'rotation_rate_alpha',
    'rot_beta': 'rotation_rate_beta',
    'rot_gamma': 'rotation_rate_gamma',
    'reading_timestamp': 'timestamp_ms'
})

#Reordering the columns
signal_recordings_detail_df = signal_recordings_detail_df[[
    'signal_ID',
    'accel_x',
    'accel_y',
    'accel_z',
    'accel_grav_x',
    'accel_grav_y',
    'accel_grav_z',
    'rotation_rate_alpha',
    'rotation_rate_beta',
    'rotation_rate_gamma',
    'timestamp_ms'
]]

In [0]:
#Viewing signal_recording_header_df
signal_recordings_header_df

signal_ID         play_ID  ...       play_name duration_ms
0    1DlnbeuO7ggujkFLGkvG     irish_surge  ...     Irish Surge        3935
1    1IJGEH5GaHkk1lhJqa8Q   collapse_left  ...   Collapse Left        3310
2    29Ha6Y92iCipu8yPCwhZ     irish_surge  ...     Irish Surge        4384
3    2aSWziIFSvFAn0gOzmk5  touchdown_halo  ...  Touchdown Halo        4272
4    47UgyhAVQeGbf81EHWCL  touchdown_halo  ...  Touchdown Halo        3717
..                    ...             ...  ...             ...         ...
97   wH8FpscdI1uMm7VUPM7d   collapse_left  ...   Collapse Left        2141
98   xnQr3xdH4SP8uEb33vCg   collapse_left  ...   Collapse Left        2374
99   y7TAmPnBgwd1ZgINn8cz  touchdown_halo  ...  Touchdown Halo        5007
100  z7QhU8w2GZhAjkiEC1Ed  touchdown_halo  ...  Touchdown Halo        4407
101  zXrKF0R3HdNp06LYdJvq   collapse_left  ...   Collapse Left        3185

[102 rows x 6 columns]

In [0]:
#Viewing signal_recordings_detail_df
signal_recordings_detail_df

signal_ID   accel_x  ...  rotation_rate_gamma  timestamp_ms
0      1DlnbeuO7ggujkFLGkvG -0.000000  ...            14.100000             8
1      1DlnbeuO7ggujkFLGkvG  0.000000  ...             0.300000            71
2      1DlnbeuO7ggujkFLGkvG  0.100000  ...             1.300000            86
3      1DlnbeuO7ggujkFLGkvG -0.000000  ...             1.000000           103
4      1DlnbeuO7ggujkFLGkvG -0.100000  ...             1.300000           120
...                     ...       ...  ...                  ...           ...
23995  zXrKF0R3HdNp06LYdJvq -0.367309  ...            18.146954          3110
23996  zXrKF0R3HdNp06LYdJvq -4.882896  ...            -6.539347          3127
23997  zXrKF0R3HdNp06LYdJvq -1.974081  ...           -14.143733          3142
23998  zXrKF0R3HdNp06LYdJvq -1.716032  ...           -29.998447          3159
23999  zXrKF0R3HdNp06LYdJvq -0.990127  ...           -39.879176          3177

[24000 rows x 11 columns]

# Load

TODO: Actually load the data into your target database so that you can later write SQL queries and explore the data.

# Users Table

In [0]:
#Making sure timestamp columns are parsed for users_df
users_df['created_at'] = pd.to_datetime(users_df['created_at'])
users_df['updated_at'] = pd.to_datetime(users_df['updated_at'])

In [0]:
#Converting pandas dataframe to spark dataframe
users_sdf = spark.createDataFrame(users_df)

In [0]:
from pyspark.sql.types import IntegerType

#Converting age variable to integer from users_df
users_sdf = users_sdf.withColumn("age", users_sdf["age"].cast(IntegerType()))

In [0]:
#Overwriting target database table that was created for users
users_sdf.write.mode("overwrite").saveAsTable("databases.eshin2.users")

In [0]:
%sql
---Viewing users table after loading data into the table
SELECT * FROM databases.eshin2.users

user_ID active_course_ID full_name age email created_at active_course_name updated_at 3T02i8MvMYV0f7Xz7MCnvyLMpLG3 SU25-DS-60620-01 Andrew Benedum 27 abenedum@nd.edu 2025-07-09T17:05:35.042Z Databases and Data Architecture (Summer 2025) 2025-07-10T14:40:50.519Z 7hOsavOpK9hQ53r43R19b8kHxS72 SU25-DS-60620-01 Bryan Massoth 32 btmassoth@gmail.com 2025-06-15T05:06:36.240Z Databases and Data Architecture (Summer 2025) 2025-06-15T05:06:36.240Z A7P5QM0SuEh30sbaJVr4DwwQvpz2 SU25-DS-60620-01 d rd 43 daniel.r.douce@gmail.com 2025-06-15T02:40:21.079Z Databases and Data Architecture (Summer 2025) 2025-06-15T02:40:21.079Z DtFQaogasuVGQ7usVu0V4Qhn6BU2 SU25-DS-60620-01 Jade Liggett 30 jadeliggett21@gmail.com 2025-06-17T16:38:50.711Z Databases and Data Architecture (Summer 2025) 2025-06-17T16:38:50.711Z EMqtMc0U5DM40FAplfHIAWWMEuq1 SU25-DS-60620-01 Ricardo Ramirez 32 rramir22@nd.edu 2025-07-16T06:15:16.816Z Databases and Data Architecture (Summer 2025) 2025-07-16T06:15:16.816Z EMr3nqqL6ygD1MYdgxrJosFUzn63 SU25-DS-60620-01 Bridget Liesman 28 bliesman@nd.edu 2025-06-28T15:32:53.291Z Databases and Data Architecture (Summer 2025) 2025-06-28T15:32:53.291Z Gj9r95rnXdT2pSyXwA3D2mTG2iK2 SU25-DS-60620-01 Chris Frederick 46 chris@sbcodeworks.com 2025-06-17T02:18:08.788Z Databases and Data Architecture (Summer 2025) 2025-06-17T02:18:08.788Z Lpdfv7XnLMQ5gVb46Rc6K9DhgWN2 SU25-DS-60620-01 Sean Lyons 23 slyons7@nd.edu 2025-07-01T13:33:51.477Z Databases and Data Architecture (Summer 2025) 2025-07-02T01:54:43.399Z M9GfFK2s7PhEUcy4PfQvvcoJvPJ3 SU25-DS-60620-01 Austin Lee 31 wlee25@nd.edu 2025-07-07T02:28:49.233Z Databases and Data Architecture (Summer 2025) 2025-07-07T02:28:49.233Z NCMa58qu9UaHHMEbuNxzuphjm1v2 SU25-DS-60620-01 Gabby Salera 26 gsalera@nd.edu 2025-07-20T19:51:49.107Z Databases and Data Architecture (Summer 2025) 2025-07-20T19:51:49.107Z PIYoM7g2NPeWCyJzADmC8Q3AoNU2 SU25-DS-60620-01 Steven Villalon 42 steven.villalon@gmail.com 2025-07-19T20:05:44.303Z Databases and Data Architecture (Summer 2025) 2025-07-19T20:05:44.303Z Q55o2vIYKiOHUpN7hQk5oQEPrDd2 SU25-DS-60620-01 Noah DiRoberto 24 ndirober@nd.edu 2025-07-19T15:32:44.550Z Databases and Data Architecture (Summer 2025) 2025-07-25T16:09:45.737Z SlZVgkV1ElRlZJs1t5UE4rr99vE3 SU25-DS-60620-01 Christopher Frederick 46 chris.l.frederick@gmail.com 2025-06-14T15:55:30.445Z Databases and Data Architecture (Summer 2025) 2025-06-17T12:57:58.079Z WeNzNivJuegep48EQna4cuQQFcg1 SU25-DS-60620-01 Zach Stabrowski 29 zstabro4@nd.edu 2025-07-06T21:55:42.885Z Databases and Data Architecture (Summer 2025) 2025-07-07T02:53:15.518Z cIXcvPgvBdfRTzb7ibknCHrVN7x1 SU25-DS-60620-01 Jack Bremer 31 jbremer@nd.edu 2025-07-04T21:59:58.971Z Databases and Data Architecture (Summer 2025) 2025-07-04T21:59:58.971Z g7zvQ4PESCU1kPBW7oPvkTtKjq43 SU25-DS-60620-01 Jeff Goseland 44 jgoselan@nd.edu 2025-07-06T18:37:00.202Z Databases and Data Architecture (Summer 2025) 2025-07-06T18:37:43.821Z gwlEfEhe2nPNVNRrpjpJTvuC0Ig1 SU25-DS-60620-01 Simone Haywood 30 shaywoo1@nd.edu 2025-07-07T02:23:06.659Z Databases and Data Architecture (Summer 2025) 2025-07-07T02:23:06.659Z izX8B4Q6YoTSyMEbVBG95KD6F0f2 SU25-DS-60620-01 Jade Liggett 30 jligget2@nd.edu 2025-06-17T14:18:21.384Z Databases and Data Architecture (Summer 2025) 2025-06-17T16:39:30.783Z jAeDhyLhx2cXNiRoGrOBd5jbKxg2 SU25-DS-60620-01 Jake Machulcz 28 jmachulc@nd.edu 2025-07-17T23:22:48.881Z Databases and Data Architecture (Summer 2025) 2025-07-17T23:22:48.881Z jUmt1zPgyZORPZuC55z8aeGyMqJ2 SU25-DS-60620-01 Paul Drake 99 pdrake@nd.edu 2025-06-15T02:42:01.698Z Databases and Data Architecture (Summer 2025) 2025-06-15T02:42:01.698Z mvMEQgMQXBg4rZzOLhmqdGbOPXk1 SU25-DS-60620-01 Mike Mulvihill 24 mmulvih3@nd.edu 2025-07-20T19:52:58.925Z Databases and Data Architecture (Summer 2025) 2025-07-20T19:52:58.925Z n13pC0Eu2wgFT7kDPFO9mI7bJnJ2 SU25-DS-60620-01 Dinesh Prashanth Varatharajan 40 dvaratha@nd.edu 2025-06-29T00:47:39.991Z Databases and Data Architecture (Summer 2025) 2025-07-06T05:22:48.577Z nDJIvjq

# Signal Playbook Table

In [0]:
#Converting pandas dataframe to spark dataframe
signal_playbook_sdf = spark.createDataFrame(signal_playbook_df)

In [0]:
#Overwriting target database table that was created for signal_playbook
signal_playbook_sdf.write.mode("overwrite").saveAsTable("databases.eshin2.signal_playbook")

In [0]:
%sql
---Viewing signal_playbook table after loading data into the table
SELECT * FROM databases.eshin2.signal_playbook

play_ID gesture historical_context latin_code_name mechanic play_name translation play_type collapse_left < Mirrors the 1988 goal-line stand vs. Miami. Inches from the goal, the Irish defense locked in with perfect discipline and grit. This call is a tactical reminder of collective pressure and precise execution. Cuneus Deflectere A directional collapse inward from the left — used to break protection schemes and force a disrupted response from the opponent’s offense. Collapse Left Wedge Collapse Defense irish_surge N Based on the 2005 “Bush Push” vs. USC. Under extreme pressure, the Irish offense surged with urgency and power. This call reflects Notre Dame’s commitment to driving through adversity to reach the end zone. Impulsus Ferrum A forward-driving signal that initiates a direct, aggressive push — designed to break through the front line and open a clear path. Irish Surge Iron Surge Offense touchdown_halo O (Circle x2) Echoes the 1973 Sugar Bowl when the home crowd’s energy helped launch Tom Clements’ deep pass to victory. This call captures the surge created when the team and its fans are locked in together. Anima Stadium Double circular motion — boosts team tempo, sync, and field awareness. Used to elevate overall play under crowd-fueled momentum. Touchdown Halo Spirit of the Stadium 12th Man

# Signal Recordings Header Table

In [0]:
#Converting pandas dataframe to spark dataframe
signal_recordings_header_sdf = spark.createDataFrame(signal_recordings_header_df)

In [0]:
#Converting age variable to integer from users_df
signal_recordings_header_sdf = signal_recordings_header_sdf.withColumn("duration_ms", signal_recordings_header_sdf["duration_ms"].cast(IntegerType()))

In [0]:
#Overwriting target database table that was created for signal_recordings_header
signal_recordings_header_sdf.write.mode("overwrite").saveAsTable("databases.eshin2.signal_recordings_header")

In [0]:
%sql
---Viewing signal_recordings_header table after loading data into the table
SELECT * FROM databases.eshin2.signal_recordings_header

signal_ID play_ID user_ID time_stamp play_name duration_ms 1DlnbeuO7ggujkFLGkvG irish_surge A7P5QM0SuEh30sbaJVr4DwwQvpz2 2025-06-15T02:43:36.130Z Irish Surge 3935 1IJGEH5GaHkk1lhJqa8Q collapse_left yyJqKEAv0qZCzmksNJA26VVizfE3 2025-06-15T02:41:03.843Z Collapse Left 3310 29Ha6Y92iCipu8yPCwhZ irish_surge Q55o2vIYKiOHUpN7hQk5oQEPrDd2 2025-07-25T16:10:59.465Z Irish Surge 4384 2aSWziIFSvFAn0gOzmk5 touchdown_halo PIYoM7g2NPeWCyJzADmC8Q3AoNU2 2025-07-20T02:21:33.670Z Touchdown Halo 4272 47UgyhAVQeGbf81EHWCL touchdown_halo yyJqKEAv0qZCzmksNJA26VVizfE3 2025-06-15T02:44:46.322Z Touchdown Halo 3717 4Wbyk28GrZv96p9exFXf touchdown_halo mvMEQgMQXBg4rZzOLhmqdGbOPXk1 2025-07-20T19:53:45.963Z Touchdown Halo 4025 4gy7WbEGI36m14m1QIgW irish_surge PIYoM7g2NPeWCyJzADmC8Q3AoNU2 2025-07-20T02:21:17.796Z Irish Surge 3607 54F5PZ24VIXQiatpUNLY touchdown_halo PIYoM7g2NPeWCyJzADmC8Q3AoNU2 2025-07-26T01:12:57.047Z Touchdown Halo 4456 5Q3EOcGy71GobUOWdPgZ collapse_left EMr3nqqL6ygD1MYdgxrJosFUzn63 2025-07-12T17:16:01.570Z Collapse Left 2903 6BRNZql8heCWmsoLhQjI collapse_left EMr3nqqL6ygD1MYdgxrJosFUzn63 2025-07-24T21:12:02.454Z Collapse Left 1936 6BeNxvXJMB7t7cZiyfkI collapse_left yyJqKEAv0qZCzmksNJA26VVizfE3 2025-06-15T02:41:14.604Z Collapse Left 1770 6kKbmHIlPZputvgUGwKa irish_surge PIYoM7g2NPeWCyJzADmC8Q3AoNU2 2025-07-26T01:14:31.528Z Irish Surge 2902 78usKvy4Yp9FLMNh5d6D touchdown_halo Lpdfv7XnLMQ5gVb46Rc6K9DhgWN2 2025-07-02T01:56:11.026Z Touchdown Halo 4420 7WMTZ00d9qmA0izgSrva collapse_left sNDSCcBtCDbGlzCaRwVVOFfQDTF2 2025-06-16T17:11:06.652Z Collapse Left 1748 85Pvi5mloW2PV0igRHlg collapse_left SlZVgkV1ElRlZJs1t5UE4rr99vE3 2025-06-16T16:38:43.451Z Collapse Left 1746 8aas0YzVO4fjXTTafQIK collapse_left A7P5QM0SuEh30sbaJVr4DwwQvpz2 2025-06-15T02:43:51.674Z Collapse Left 2692 A4mlfmfvvLXobGFZYXMl irish_surge SlZVgkV1ElRlZJs1t5UE4rr99vE3 2025-06-15T02:51:19.607Z Irish Surge 2533 Au3I2vBLCA9hfElsPUXx touchdown_halo sNDSCcBtCDbGlzCaRwVVOFfQDTF2 2025-06-27T01:50:44.366Z Touchdown Halo 3712 Avr43lXJbov4LGbDDkCv collapse_left jUmt1zPgyZORPZuC55z8aeGyMqJ2 2025-06-15T02:45:19.170Z Collapse Left 2353 BLjMutelDfEJDP72Mj1Y touchdown_halo A7P5QM0SuEh30sbaJVr4DwwQvpz2 2025-06-15T02:42:18.072Z Touchdown Halo 4087 CMm8sLBOUW38WWCesZIc touchdown_halo PIYoM7g2NPeWCyJzADmC8Q3AoNU2 2025-07-26T01:12:43.029Z Touchdown Halo 4458 CpVz5MMPcSIu2qknfqL5 touchdown_halo A7P5QM0SuEh30sbaJVr4DwwQvpz2 2025-06-15T02:42:06.083Z Touchdown Halo 5007 Da3rrGl3jP7bOzsarG31 collapse_left PIYoM7g2NPeWCyJzADmC8Q3AoNU2 2025-07-19T20:14:01.379Z Collapse Left 2553 FH4JhbzbTxl5rmDndi5d touchdown_halo SlZVgkV1ElRlZJs1t5UE4rr99vE3 2025-06-15T02:51:59.146Z Touchdown Halo 4055 GHvKdwUQPGlt3JJzVMZO irish_surge WeNzNivJuegep48EQna4cuQQFcg1 2025-07-22T00:36:18.802Z Irish Surge 2849 GMU0N1fL65ifmgHARUxP touchdown_halo SlZVgkV1ElRlZJs1t5UE4rr99vE3 2025-06-15T02:51:39.547Z Touchdown Halo 3355 HYkTECkijEGb9udm9nkd irish_surge EMr3nqqL6ygD1MYdgxrJosFUzn63 2025-07-12T17:16:14.709Z Irish Surge 2600 IL7pBQEeF2yPmWLGjsqw collapse_left A7P5QM0SuEh30sbaJVr4DwwQvpz2 2025-06-15T02:40:51.732Z Collapse Left 2371 IiSlLCv6Vcqk8qEpUPud irish_surge 7hOsavOpK9hQ53r43R19b8kHxS72 2025-06-15T05:33:31.633Z Irish Surge 5003 ImK2b1dRd6trcjf3stkN irish_surge 3T02i8MvMYV0f7Xz7MCnvyLMpLG3 2025-07-10T14:51:51.642Z Irish Surge 4394 JreqV80lTYXk7pxSG4mj irish_surge yyJqKEAv0qZCzmksNJA26VVizfE3 2025-06-15T02:41:39.327Z Irish Surge 4884 KFqDecAjmljCPTwVCWn7 irish_surge 7hOsavOpK9hQ53r43R19b8kHxS72 2025-06-15T05:33:14.550Z Irish Surge 5008 LVhtMcAvZA25Ez8xcg2g collapse_left Gj9r95rnXdT2pSyXwA3D2mTG2iK2 2025-06-17T02:18:42.106Z Collapse Left 2045 LZw2JufycUq9bEK1e2ar irish_surge Lpdfv7XnLMQ5gVb46Rc6K9DhgWN2 2025-07-02T01:55:55.338Z Irish Surge 3577 LnpFrUtit9nckLaVJI37 collapse_left 7hOsavOpK9hQ53r43R19b8kHxS72 2025-06-15T05:42:10.027Z Collapse Left 2753 LrArDuXEy6HzQ0331kjM irish_surge A7P5QM0SuEh30sbaJVr4DwwQvpz2 2025-06-15T02:43:07.288Z Irish Surge 2711 NOk7qZrwRGORHmuWsLvq touchdown_halo A7P5QM0SuEh30sbaJVr4DwwQvpz2 2025-06-15T02:42:5

# Signal Recordings Detail Table

In [0]:
#Converting pandas dataframe to spark dataframe
signal_recordings_detail_sdf = spark.createDataFrame(signal_recordings_detail_df)

In [0]:
from pyspark.sql.functions import col

#Casting variables from signal_recordings_detail_sdf
signal_recordings_detail_sdf = signal_recordings_detail_sdf.select(
    col("signal_ID").cast("string"),
    "accel_x",
    "accel_y",
    "accel_z",
    "accel_grav_x",
    "accel_grav_y",
    "accel_grav_z",
    "rotation_rate_alpha",
    "rotation_rate_beta",
    "rotation_rate_gamma",
    col("timestamp_ms").cast("integer")
)

In [0]:
#Overwriting target database table that was created for signal_recordings_detail
signal_recordings_detail_sdf.write.mode("overwrite").saveAsTable("databases.eshin2.signal_recordings_detail")

In [0]:
%sql
---Viewing signal_recordings_detail table after loading data into the table
SELECT * FROM databases.eshin2.signal_recordings_detail

signal_ID accel_x accel_y accel_z accel_grav_x accel_grav_y accel_grav_z rotation_rate_alpha rotation_rate_beta rotation_rate_gamma timestamp_ms O6BXBNcgv1f3Usl7FV9q 0.2881272060394287 -0.28390695799589155 -0.2658110370740294 3.48296398832947 -9.159016697362064 -2.9483111681833862 71.8654882580683 -88.28175230554557 20.588029186852456 339 O6BXBNcgv1f3Usl7FV9q 0.18763211111128328 0.15019757573008535 -0.5871715274125338 3.3013042296260595 -8.781032694786786 -3.1772569941967723 54.334482696531595 -55.254037894679584 6.722498004255983 356 O6BXBNcgv1f3Usl7FV9q 0.3265852392494678 0.07619242832064628 0.5032318459659815 3.3928824431270357 -8.897002422222494 -1.9967659381359815 31.34404204460658 -23.69015084371051 2.031447669549886 373 O6BXBNcgv1f3Usl7FV9q -0.23237346237450837 -0.2451367900967598 0.7052996019259095 2.825756217138469 -9.232789789581298 -1.7524077311962842 10.524675204339436 3.3631789574553435 0.5125725067589589 389 O6BXBNcgv1f3Usl7FV9q -0.05525339292734861 2.2504092752933502E-4 0.7761234889507294 3.000083733257651 -8.992321575817465 -1.667114004792273 -4.981381612642652 20.092487009736985 8.71195922031733 406 O6BXBNcgv1f3Usl7FV9q -0.4223617812231183 -0.18167641757726669 0.16981763747930526 2.6264386366695165 -9.177123431938886 -2.2709015898324547 -5.741696499820492 24.179950539281293 6.288863381117037 422 O6BXBNcgv1f3Usl7FV9q -0.1482028947815299 -0.0411304672896862 -0.8869276503168046 2.902520015606284 -9.040054802373051 -3.3123793120004237 4.744463694676066 19.176196642012265 4.400999948299159 439 O6BXBNcgv1f3Usl7FV9q 0.0780018158301711 0.1752361553966999 -1.0803002047762273 3.127873954607546 -8.834303097203373 -3.467104594288021 16.95756336938995 10.829924896083769 4.649067296312144 456 O6BXBNcgv1f3Usl7FV9q -0.10726795006394385 0.07290273912549018 -0.2009754306785762 2.9330457945123314 -8.95745542961955 -2.5203477675609287 18.817155795459495 1.9201883702820213 3.505335471207407 472 O6BXBNcgv1f3Usl7FV9q -0.41760201947540043 -0.22821429686844347 0.42334114764928815 2.6209020453304053 -9.268851283043622 -1.8580517333202062 10.701478919873448 3.7854837908651193 -1.3412678328123817 489 O6BXBNcgv1f3Usl7FV9q -0.5381719341829418 -0.20241817683279514 0.408866193703562 2.5128634031549093 -9.243861218693851 -1.8525152881115674 3.295802129500929 6.71312485028061 -5.71183405899555 506 O6BXBNcgv1f3Usl7FV9q -0.030486031417548656 0.23578794699311256 0.18629355598390102 3.038391252081096 -8.802730147331953 -2.062606629920751 0.8321879005968263 11.242943020099855 -0.8912329649808826 522 O6BXBNcgv1f3Usl7FV9q 0.4511702348172664 0.43027708439230916 -0.6292910057395696 3.521720712225139 -8.61269039055705 -2.857930493903905 6.702907314169094 14.377387693431345 6.173245780828469 539 O6BXBNcgv1f3Usl7FV9q 0.21944939113259315 0.3132534639894962 -0.35659780793637036 3.2791584487915038 -8.74033243560791 -2.5568599274002013 10.832265943421792 6.256208673582028 7.1284174272903105 556 O6BXBNcgv1f3Usl7FV9q -0.24218729264140126 0.009682605102658271 0.06926759749352931 2.8007664450496432 -9.058909724968672 -2.092085091730952 8.113391323535033 1.9031739421726963 4.721871136448956 573 O6BXBNcgv1f3Usl7FV9q -0.5739946504533291 -0.3464303419262171 0.2610124046206474 2.4654285750240086 -9.420134900444745 -1.8837889627754687 4.1948575820721805 4.558600160094856 -0.5743476724594633 591 O6BXBNcgv1f3Usl7FV9q -0.4360331637009978 -0.2560977445721626 0.1691010136425495 2.609978792516887 -9.329754372295737 -1.9665389960460364 0.2663381307231962 5.12595323859655 -2.0263845783842025 606 O6BXBNcgv1f3Usl7FV9q -0.030424072097241878 0.14197978248298168 -0.2749716641291976 3.0207340148374437 -8.931868568420409 -2.4024333357982335 1.9521660353155517 9.465275298030024 4.67071430022603 623 O6BXBNcgv1f3Usl7FV9q 0.3365843629553914 0.2601473122239113 -0.43426323141902684 3.3756747032165526 -8.821436016845702 -2.545935797803849 5.073007746584727 8.155994628482988 8.191645654629514 639 O6BXBNcgv1f3Usl7FV9q -0.1203676701337099 -0.09237959301173686 -0.29703531963825225 2.90730871118

# Primary and Foreign Key Constraints

Primary and foreign key constraints are not supported in standard Spark-managed tables.

I ended up using ALTER TABLE SQL statements directly to add informational primary and foreign keys.

In [0]:
%sql
---Adding primary key constraint to the users table
ALTER TABLE databases.eshin2.users ADD CONSTRAINT users_pk PRIMARY KEY (user_ID)

In [0]:
%sql
---Adding primary key constraint to the signal_playbook table
ALTER TABLE databases.eshin2.signal_playbook ADD CONSTRAINT signal_playbook_pk PRIMARY KEY (play_ID)

In [0]:
%sql
---Adding primary key constraint to the signal_recordings_header table
ALTER TABLE databases.eshin2.signal_recordings_header ADD CONSTRAINT signal_recordings_header_pk PRIMARY KEY (signal_ID)

In [0]:
%sql
---Adding first foreign key constraint to the signal_recordings_header table
ALTER TABLE databases.eshin2.signal_recordings_header ADD CONSTRAINT signal_recordings_header_playbook_fk FOREIGN KEY (play_ID) REFERENCES databases.eshin2.signal_playbook(play_ID)

In [0]:
%sql
---Adding second foreign key constraint to the signal_recordings_header table
ALTER TABLE databases.eshin2.signal_recordings_header ADD CONSTRAINT signal_recordings_header_users_fk FOREIGN KEY (user_ID) REFERENCES databases.eshin2.users(user_ID)

In [0]:
%sql
---Adding primary constraint to the signal_recordings_detail table
ALTER TABLE databases.eshin2.signal_recordings_detail ADD CONSTRAINT signal_recordings_detail_pk PRIMARY KEY (signal_ID)

In [0]:
%sql
---Adding foreign key constraint to the signal_recordings_detail table
ALTER TABLE databases.eshin2.signal_recordings_detail ADD CONSTRAINT signal_recordings_detail__header_fk FOREIGN KEY (signal_ID) REFERENCES databases.eshin2.signal_recordings_header(signal_ID)